In [1]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append("../../")
from utils import *

/opt/conda/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
bpm = 130.0 # beat per minute


beat_per_bar = 8
bar_per_emphasis = 2

noise_buildup = True
n_bars_buildup = 8

progression = [
    {"part":"intro", "duration": 4 , "tracks":[("base", "no") , ("chords", "no") , ("drums1", "no") , ("drums2", "no") , ("melody1", "yes"), ("melody2", "no") ]},
    {"part":"verse", "duration": 12, "tracks":[("base", "yes"), ("chords", "yes"), ("drums1", "yes"), ("drums2", "no") , ("melody1", "yes"), ("melody2", "no") ]},
    {"part":"pause", "duration": 4,  "tracks":[("base", "yes"), ("chords", "no") , ("drums1", "no") , ("drums2", "no") , ("melody1", "no") , ("melody2", "no") ]},
    {"part":"verse", "duration": 12, "tracks":[("base", "yes"), ("chords", "yes"), ("drums1", "yes"), ("drums2", "yes"), ("melody1", "yes"), ("melody2", "yes")]}
]

backbone = generate_backbone(bpm,beat_per_bar,bar_per_emphasis, noise_buildup, n_bars_buildup, progression)

handling {'part': 'intro', 'duration': 4, 'tracks': [('base', 'no'), ('chords', 'no'), ('drums1', 'no'), ('drums2', 'no'), ('melody1', 'yes'), ('melody2', 'no')]}
handling {'part': 'verse', 'duration': 12, 'tracks': [('base', 'yes'), ('chords', 'yes'), ('drums1', 'yes'), ('drums2', 'no'), ('melody1', 'yes'), ('melody2', 'no')]}
handling {'part': 'pause', 'duration': 4, 'tracks': [('base', 'yes'), ('chords', 'no'), ('drums1', 'no'), ('drums2', 'no'), ('melody1', 'no'), ('melody2', 'no')]}
handling {'part': 'verse', 'duration': 12, 'tracks': [('base', 'yes'), ('chords', 'yes'), ('drums1', 'yes'), ('drums2', 'yes'), ('melody1', 'yes'), ('melody2', 'yes')]}


In [34]:
drum_generator_1 = produce_drum_generator()
drum_generator_2 = produce_drum_generator()

In [49]:
first_drum_1 = True
first_drum_2 = True


current_length = 0.0

for b in backbone:
    
    t =  (1 - b['buildup_factor']) + b['buildup_factor']**2 * 2
    
    clonk = 49 if b["final_bar"] else 42

    nsteps = 16
    beams = 128

    #
    # Drum 1
    #
    if b["drums1"] == 1.0:
        if first_drum_1:
            drum_seq = generate_one_bar_sequence(generator=drum_generator_1, qpm=bpm, temp=t, number_of_steps=nsteps, beam_size=beams, primer = [(35,),(),(clonk,),()])
            
            retimed = music_pb2.NoteSequence()
            retimed.CopyFrom(drum_seq)

            for note in retimed.notes:
                note.start_time += current_length
                note.end_time += current_length
                retimed.total_time += current_length
                
            full_drum_seq1 = retimed
            
            first_drum_1 = False
            
            print("number of notes (drum_seq1) = " + str(len(full_drum_seq1.notes)))
            
        else:
            drum_seq = generate_one_bar_sequence(generator=drum_generator_1, qpm=bpm, temp=t, number_of_steps=nsteps, beam_size=beams, primer = [(35,),(),(clonk,),()])
            full_drum_seq1 = adjust_sequence_times_and_merge(full_drum_seq1,drum_seq,current_length)
            print("number of notes (drum_seq1) = " + str(len(full_drum_seq1.notes)))
        

            
    #
    # Drum 1
    #    
    if b["drums2"] == 1.0:
        if first_drum_2:
            drum_seq = generate_one_bar_sequence(generator=drum_generator_2, qpm=bpm, temp=t, number_of_steps=nsteps, beam_size=beams, primer = [(46,),(42,),(46,clonk,),(42,)])
            
            retimed = music_pb2.NoteSequence()
            retimed.CopyFrom(drum_seq)

            for note in retimed.notes:
                note.start_time += current_length
                note.end_time += current_length
                retimed.total_time += current_length
                
            full_drum_seq2 = retimed
            
            first_drum_2 = False
            
            print("number of notes (drum_seq2) = " + str(len(full_drum_seq2.notes)))
            
        else:
            drum_seq = generate_one_bar_sequence(generator=drum_generator_2, qpm=bpm, temp=t, number_of_steps=nsteps, beam_size=beams, primer = [(46 ,),(42,),(46 ,clonk,),(42,)])
            full_drum_seq2 = adjust_sequence_times_and_merge(full_drum_seq2,drum_seq,current_length)
            print("number of notes (drum_seq2) = " + str(len(full_drum_seq2.notes)))
            
    current_length += compute_time(qpm=bpm,nsteps=nsteps)
    print("duration = " + str(current_length))
    
full_drum_seq1.MergeFrom(full_drum_seq2)

full_drum_seq = full_drum_seq1

duration = 1.8461538461538463
duration = 3.6923076923076925
duration = 5.538461538461538
duration = 7.384615384615385
Using primer[(35,), (), (42,), ()]
INFO:tensorflow:Beam search yields sequence with log-likelihood: -7.771124 
number of notes (drum_seq1) = 6
duration = 9.230769230769232
Using primer[(35,), (), (42,), ()]
INFO:tensorflow:Beam search yields sequence with log-likelihood: -7.771124 
number of notes (drum_seq1) = 12
duration = 11.076923076923078
Using primer[(35,), (), (42,), ()]
INFO:tensorflow:Beam search yields sequence with log-likelihood: -7.771124 
number of notes (drum_seq1) = 18
duration = 12.923076923076925
Using primer[(35,), (), (42,), ()]
INFO:tensorflow:Beam search yields sequence with log-likelihood: -7.771124 
number of notes (drum_seq1) = 24
duration = 14.769230769230772
Using primer[(35,), (), (42,), ()]
INFO:tensorflow:Beam search yields sequence with log-likelihood: -7.771124 
number of notes (drum_seq1) = 30
duration = 16.615384615384617
Using primer[(

In [50]:
mm.play_sequence(full_drum_seq, mm.midi_synth.fluidsynth)

In [46]:
len(full_drum_seq.notes)

352

In [35]:
pd.DataFrame.from_records([dict(n.ListFields()) for n in list(full_drum_seq.notes)])

<google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c5398f0>  \
0                                                 35                           
1                                                 49                           
2                                                 38                           
3                                                 38                           
4                                                 38                           
5                                                 38                           

   <google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c6b4c50>  \
0                                                100                           
1                                                100                           
2                                                100                           
3                                                100                           
4                                                100                           
5                                                100                           

   <google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c7a5ad0>  \
0                                           0.115385                           
1                                           0.346154                           
2                                          58.730769                           
3                                          58.846154                           
4                                          58.961538                           
5                                          59.076923                           

   <google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c7a5570>  \
0                                                  9                           
1                                                  9                           
2                                                  9                           
3                                                  9                           
4                                                  9                           
5                                                  9                           

  <google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c7a5530>  \
0                                               True                          
1                                               True                          
2                                               True                          
3                                               True                          
4                                               True                          
5                                               True                          

   <google.protobuf.pyext._message.FieldDescriptor object at 0x7f6d3c4c85b0>  
0                                                NaN                          
1                                           0.230769                          
2                                          58.615385                          
3                                          58.730769                          
4                                          58.846154                          
5                                          58.961538